# Predict expression modulation targets

Cameo provides algorithms to search for genes or reactions that can be over or down regulated in order to achieve a given biological objective.

In [1]:
from cameo import models

Load the E. coli core model.

In [2]:
model = models.bigg.e_coli_core

## Flux Scanning based on Enforced Objective Flux

In [3]:
from cameo.strain_design.deterministic.flux_variability_based import FSEOF

In [4]:
fseof = FSEOF(model)

In [5]:
fseof.run(target=model.reactions.EX_succ_e)

## Differential flux variability analysis

Compares flux ranges of a reference model to a set of models that have been parameterized to lie on a grid of evenly spaced points in the n-dimensional production envelope (n being the number of reaction bounds to be varied).

In [6]:
from cameo.flux_analysis.analysis import phenotypic_phase_plane
from cameo.strain_design.deterministic import DifferentialFVA

### Succinate production

The production envelope looks like this.

In [7]:
production_envelope = phenotypic_phase_plane(model, 
                                             variables=[model.reactions.BIOMASS_Ecoli_core_w_GAM],
                                             objective=model.metabolites.succ_e)
production_envelope.plot(height=400)

Set up a model that represents a reference state (in this case a model with a constrained growth rate).

In [8]:
model.reactions.EX_o2_e.lower_bound = 0
reference_model = model.copy()
biomass_rxn = reference_model.reactions.BIOMASS_Ecoli_core_w_GAM
biomass_rxn.lower_bound = 0.
target = reference_model.metabolites.succ_e

Set up the differential flux variability analysis strain design method.

In [9]:
diffFVA = DifferentialFVA(design_space_model=model,
                          reference_model=reference_model,
                          objective=target,
                          variables=[biomass_rxn],
                          normalize_ranges_by=biomass_rxn,
                          points=10)

Run differential flux variability analysis (only on the surface of the production envelope)

In [10]:
%time result = diffFVA.run(surface_only=True)
result.plot()

CPU times: user 1.49 s, sys: 32.3 ms, total: 1.52 s
Wall time: 2.16 s


In [11]:
result.plot(5, variables=['FBP', 'G6PDH2r', 'PGL', 'PGK'])

In [12]:
result

upper_bound  lower_bound gaps normalized_gaps     KO flux_reversal  \
ACALD  -9.10733e-16 -9.10733e-16    0               0  False         False   
ACALDt            0            0    0               0  False         False   
ACKr       -8.69634     -8.69634    0          82.443  False         False   
ACONTa     0.101495     0.101495    0               0  False         False   
ACONTb     0.101495     0.101495    0               0  False         False   
ACt2r      -8.69634     -8.69634    0          82.443  False         False   
ADK1       0.583116     0.583116    0               0  False         False   
...             ...          ...  ...             ...    ...           ...   
SUCDi       990.126            0    0               0  False         False   
SUCOAS            0 -1.88738e-14    0               0  False         False   
TALA     -0.0168296   -0.0168296    0       -0.141033  False         False   
THD2        1.61298      1.61298    0               0  False         False   
TKT1     -0.0168296   -0.0168296    0       -0.141033  False         False   
TKT2     -0.0507897   -0.0507897    0       -0.425623  False         False   
TPI         9.90643      9.90643    0         95.3064  False         False   

       suddenly_essential  
ACALD                True  
ACALDt               True  
ACKr                 True  
ACONTa              False  
ACONTb              False  
ACt2r                True  
ADK1                False  
...                   ...  
SUCDi               False  
SUCOAS               True  
TALA                 True  
THD2                False  
TKT1                 True  
TKT2                 True  
TPI                 False  

[76 rows x 7 columns]

In [13]:
result.display_on_map(5, map_name="iJO1366.Central metabolism")